In [1]:
import pandas as pd
import numpy as np

In [ ]:
df = pd.read_csv("../../data/processed_new_data.csv", header=0)

## Text Preprocessing

Before the text is fed into the classifier, the following steps are taken:

1. Detect language
2. Translate into English
3. Lemmatization
4. Remove punctuation but not numbers
5. Stop word removal
6. Join strings separated by a space
7. Converts the string into lower case characters
8. Converts everything into a string

In [2]:
import nltk

from nltk.stem.wordnet import WordNetLemmatizer
import string
import re
from nltk.corpus import wordnet as wn
nltk.download('wordnet')
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package wordnet to /home/deepl/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/deepl/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

## Preprocessing Functions

In [3]:
nltk_wordnet_tag_map = {
    'NN': wn.NOUN,
    'NNS': wn.NOUN,
    'VBP': wn.VERB,
    'VBG': wn.VERB,
    'JJ': wn.ADJ,
}

from functools import reduce

def compose(*functions):
    def compose2(f1, f2):
        """Compose two functions"""
        return lambda *args: f1(f2(*args))
    return reduce(compose2, functions)

def translate_to_english_txt(row):
    text = row["excerpt"]
    try:
        if langid.classify(text)[0] != 'en':
            trans = googletrans.client.Translator()
            return trans.translate(text, 'en').text
        return text
    except Exception as e:
        return ''
    
def lemmatize(row, lemmatizer=WordNetLemmatizer()):
    text = row
    splitted = text if type(text) == list else str(text).split()
    splitted = list(map(lambda x: str(x).lower(), splitted))
    tagged = nltk.pos_tag(splitted)
    lemmatized = []
    for word, tag in tagged:
        wnet_tag = nltk_wordnet_tag_map.get(tag)
        if wnet_tag:
            lemmatized.append(lemmatizer.lemmatize(word, wnet_tag))
        else:
            lemmatized.append(word)
    return ' '.join(lemmatized)

def rm_punc_not_nums(inp, col=None):
    """Remove punctuation unless it's a number for either a df (and col)
    or single entry
    """
    punc = string.punctuation
    transtable = str.maketrans("", "", punc)

    def sing_rm(phr):
        """Remove for a single entity"""
        return ' '.join([re.sub('\W+', '', i).translate(transtable) if not (
                    all(j.isdigit() or j in punc for j in i)
                    and
                    any(j.isdigit() for j in i)
                ) else re.sub('\W+', '', i)
                for i in str(phr).split(' ')]
        )
    if col and isinstance(inp, pd.core.frame.DataFrame):
        return inp.filter(like=col).applymap(lambda phr: sing_rm(phr))
    elif isinstance(inp, str):
        return sing_rm(inp)
    else:
        raise Exception('Not a vaild type')


def rm_stop_words_txt(txt, swords=nltk.corpus.stopwords.words('english')):
    """ Remove stop words from given text """
    return ' '.join(
        [token for token in str(txt).split(' ')
            if token.lower() not in swords]
    )

## Sanity Check

In [4]:
data = {"excerpt": "The 2 quick brown foxes jumped over the lazy dogs!"}

def preprocess(row):
        inp = row["excerpt"]
        inp = lemmatize(inp)
        func = compose(
            rm_punc_not_nums,
            rm_stop_words_txt,
            ' '.join,
            str.split,
            str.lower,
            str
        )
        
        return func(inp)

preprocess(data)

'2 quick brown fox jumped lazy dogs'

## Model Selection Preparation

In [ ]:
df = pd.read_csv("../../data/all_en_processed_sectors_subsectors.csv")

In [ ]:
df.drop(["Unnamed: 0", "Unnamed: 0.1"], axis=1, inplace=True)

In [ ]:
df["preprocessed_excerpt"] = df.apply(preprocess, axis=1)

In [ ]:
merged_df = pd.DataFrame(df.groupby('preprocessed_excerpt')["sector"].apply(set)).reset_index()

In [ ]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.naive_bayes import MultinomialNB
from sklearn.pipeline import Pipeline

In [ ]:
text_clf = Pipeline([
            ('vect', CountVectorizer(ngram_range=(1, 2))),
            ('tfidf', TfidfTransformer(use_idf=False)),
            ('clf', MultinomialNB(alpha=0.01, fit_prior=False))
        ])

In [ ]:
# Flatten list
temp_list = [list(x) for x in list(merged_df["sector"])]

In [ ]:
category_columns = [j for sub in temp_list for j in sub]
category_columns = list(set(category_columns))

In [ ]:
# Add categories as columns
category_df = pd.concat([merged_df,pd.DataFrame(columns=category_columns)])

In [ ]:
category_df.fillna(value=0, inplace=True)

In [ ]:
def update(row):
    for each in list(row["sector"]):
        row[each] = 1
    return row

In [ ]:
category_df = category_df.apply(update, axis=1)

In [ ]:
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.multiclass import OneVsRestClassifier

text_clf = Pipeline([
            ('vect', CountVectorizer(ngram_range=(1, 2))),
            ('tfidf', TfidfTransformer(use_idf=False))
        ])

In [ ]:
features = text_clf.fit_transform(category_df["preprocessed_excerpt"])
labels = category_df.iloc[:,:12]

In [ ]:
labels = np.array(labels)

In [ ]:
from sklearn.linear_model import RidgeClassifierCV
import sklearn.model_selection as ms
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import cross_validate
from sklearn.model_selection import cross_val_score

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline

In [ ]:
def model_cv(data, labels, model):
    print ("Cross Validating: {0}".format(model["name"]))
    print ("Data shape", data.shape)
    print ("Labels shape", labels.shape)
    scoring = ['accuracy', 'precision_macro', 'recall_macro']
    scores = cross_validate(model["model"], data, labels, scoring=scoring, cv=ms.KFold(n_splits=10, shuffle = True, random_state=7), return_train_score=False)
    k = list(range(10))
    plt.scatter(k, scores['test_accuracy'])
    plt.scatter(k, scores['test_precision_macro'])
    plt.scatter(k, scores['test_recall_macro'])
    plt.ylabel("Percentage")
    plt.xlabel("Iteration")
    plt.title("{0} 10 Folds Cross Validation".format(model["name"]))
    plt.legend(['Testing Accuracy', 'Testing Precision', 'Testing Recall'], loc='upper left')

In [ ]:
labels

In [ ]:
from sklearn.multiclass import OneVsRestClassifier
from sklearn.svm import SVC
from sklearn.naive_bayes import GaussianNB

In [ ]:
models = [
#     {
#         "name": "MLP",
#         "model": MLPClassifier(activation='logistic', learning_rate='adaptive', verbose=True, early_stopping=True)
#     },
#     {
#         "name": "GaussianNB - OVR",
#         "model": OneVsRestClassifier(GaussianNB())
#     },
    {
        "name": "Linear SVC",
        "model": OneVsRestClassifier(SVC())
    },
    
]

for model in models:
    model_cv(features, labels, model)

In [ ]:
models[0]["model"]

In [5]:
df = pd.read_csv("../../data/all_en_processed_sectors_subsectors.csv")
df.drop(["Unnamed: 0", "Unnamed: 0.1"], axis=1, inplace=True)
df["preprocessed_excerpt"] = df.apply(preprocess, axis=1)

In [ ]:
print(len(df))
df.drop_duplicates(inplace=True)
print(len(df))

In [ ]:
np.where((df["preprocessed_excerpt"] == "112500 child five risk acute malnutrition"))[0][0]

## Doc2Vec

In [6]:
import gensim

In [7]:
from sklearn.model_selection import train_test_split
train, test = train_test_split(df, test_size=0.1, random_state=42)

In [8]:
def tokenize_text(text):
    tokens = []
    for sent in nltk.sent_tokenize(text):
        for word in nltk.word_tokenize(sent):
            if len(word) < 2:
                continue
            tokens.append(word.lower())
    return tokens

In [9]:
from gensim.models.doc2vec import TaggedDocument
nltk.download('punkt')
train_tagged = train.apply(
    lambda r: TaggedDocument(words=tokenize_text(r['preprocessed_excerpt']), tags=[r.sector]), axis=1)
test_tagged = test.apply(
    lambda r: TaggedDocument(words=tokenize_text(r['preprocessed_excerpt']), tags=[r.sector]), axis=1)

[nltk_data] Downloading package punkt to /home/deepl/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


AttributeError: 'TaggedDocument' object has no attribute 'values'

In [188]:
from gensim.models import Doc2Vec
model_dbow = Doc2Vec(dm=0, vector_size=50, negative=5, hs=0, min_count=2, sample = 0)
model_dbow.build_vocab([x for x in train_tagged.values])

In [189]:
from sklearn import utils
for epoch in range(10):
    model_dbow.train(utils.shuffle([x for x in train_tagged.values]), total_examples=len(train_tagged.values), epochs=1)
    model_dbow.alpha -= 0.002
    model_dbow.min_alpha = model_dbow.alpha

In [190]:
def vec_for_learning(model, tagged_docs):
    sents = tagged_docs.values
    targets, regressors = zip(*[(doc.tags[0], model.infer_vector(doc.words, steps=20)) for doc in sents])
    return targets, regressors

In [20]:
labels, features = vec_for_learning(model_dbow, train_tagged)
y_test, X_test = vec_for_learning(model_dbow, test_tagged)

In [ ]:
from sklearn.metrics.pairwise import cosine_distances, cosine_similarity

In [ ]:
print (cosine_similarity(vector1.reshape(1,-1), vector2.reshape(1, -1)))

In [ ]:
sims = model.docvecs.most_similar([vector1], topn=len(model.docvecs))

In [ ]:
sims

In [ ]:
sims = model.docvecs.most_similar([vector1], topn=len(model.docvecs))

In [ ]:
def getVector(row):
    return model.infer_vector(row["preprocessed_excerpt"])

In [ ]:
df["feature_vector"] = df.apply(getVector, axis=1)

In [ ]:
df.to_csv("processed_with_vectors.csv")

In [ ]:
from sklearn.externals import joblib
model = joblib.load('doc2vec.pkl')

In [ ]:
df.drop(["subsector"], inplace=True, axis=1)

In [ ]:
df

In [ ]:
dummies = pd.get_dummies(df["sector"])

In [ ]:
oh_df = pd.concat([dummies, df], axis=1)

In [ ]:
oh_df

In [ ]:
oh_df["feature_vector"] = oh_df["feature_vector"].apply(lambda x: x.strip())

In [ ]:
features = np.array(list(oh_df["feature_vector"]))

In [ ]:
features

In [ ]:
oh_df["sector"] = oh_df["sector"].astype("category", copy=False)

In [ ]:
from sklearn.neighbors import KNeighborsClassifier

In [ ]:
labels = np.array(oh_df.iloc[:,:12])

In [ ]:
clf = KNeighborsClassifier(n_neighbors=5)

In [ ]:
models = {"name": "KNN-5", "model": clf}
model_cv(data=features, labels=labels, model=models)

In [ ]:
from sklearn.model_selection import train_test_split

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(features, labels, test_size=0.33, random_state=42)

In [ ]:
from sklearn.metrics import classification_report
clf.fit(X_train, y_train)
results = clf.predict(X_test)
print (classification_report(results, y_test))

In [ ]:
from sklearn.ensemble import RandomForestClassifier
clf = RandomForestClassifier(n_estimators=300)
clf.fit(X_train, y_train)
results = clf.predict(X_test)

In [ ]:
from sklearn.metrics import classification_report, accuracy_score, f1_score
from sklearn.linear_model import LogisticRegression

logreg = LogisticRegression(C=1, solver='lbfgs', multi_class='multinomial')
logreg.fit(X_train, y_train)
yhat = logreg.predict(X_test)

In [ ]:
print('Testing accuracy %s' % accuracy_score(y_test, results))
print('Testing F1 score: {}'.format(f1_score(y_test, results, average='weighted')))
print (classification_report(y_pred=results, y_true=y_test))

Agriculture       0.45      0.39      0.42       134
       Cross       0.35      0.18      0.23       204
   Education       0.86      0.59      0.70       252
        Food       0.64      0.78      0.70       939
      Health       0.77      0.83      0.80      1032
  Livelihood       0.45      0.28      0.35       239
    Logistic       0.49      0.22      0.30        93
         NFI       0.76      0.35      0.47       107
   Nutrition       0.80      0.64      0.71       219
  Protection       0.71      0.84      0.77       917
     Shelter       0.62      0.66      0.64       423
        WASH       0.68      0.63      0.65       381

In [ ]:
print('Testing accuracy %s' % accuracy_score(y_test, yhat))
print('Testing F1 score: {}'.format(f1_score(y_test, yhat, average='weighted')))
print (classification_report(y_pred=yhat, y_true=y_test))

In [ ]:
!pip3 install xgboost --user

In [274]:
from sklearn.ensemble import RandomForestClassifier


rf = RandomForestClassifier(n_estimators=300)

In [275]:
rf.fit(np.array(list(features.values)), labels)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=300, n_jobs=None,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False)

In [261]:
test_array = np.array(list(features.values))
test_array.shape

(14819, 60)

In [276]:
X_test = np.array(list(test["combined_vector"]))
yhat = rf.predict(np.array(X_test))

In [277]:
from sklearn.metrics import accuracy_score, f1_score, classification_report
print('Testing accuracy %s' % accuracy_score(y_test, yhat))
print('Testing F1 score: {}'.format(f1_score(y_test, yhat, average='weighted')))
print (classification_report(y_pred=yhat, y_true=y_test))

Testing accuracy 0.7030965391621129
Testing F1 score: 0.6854947364526756
              precision    recall  f1-score   support

 Agriculture       0.54      0.40      0.46        50
       Cross       0.48      0.20      0.28        70
   Education       0.83      0.67      0.74        72
        Food       0.71      0.83      0.77       341
      Health       0.76      0.86      0.81       336
  Livelihood       0.43      0.26      0.32        78
    Logistic       0.50      0.14      0.22        29
         NFI       0.83      0.52      0.64        29
   Nutrition       0.87      0.54      0.67        76
  Protection       0.71      0.86      0.78       292
     Shelter       0.61      0.67      0.64       141
        WASH       0.68      0.56      0.62       133

   micro avg       0.70      0.70      0.70      1647
   macro avg       0.66      0.54      0.58      1647
weighted avg       0.69      0.70      0.69      1647



In [55]:
len(df[df["sector"] == "Agriculture"])

461

In [59]:
!pip3 install spacy --user

In [60]:
import spacy


In [63]:
!python3 -m spacy download en --user

    100% |████████████████████████████████| 37.4MB 51.6MB/s ta 0:00:011�                   | 14.2MB 92.9MB/s eta 0:00:01 0:00:01��███████▊               | 19.5MB 55.2MB/s eta 0:00:01��██▎            | 22.5MB 58.9MB/s eta 0:00:01████████████████████        | 28.0MB 70.8MB/s eta 0:00:01��█████████████████████▍     | 30.8MB 79.1MB/s eta 0:00:01�█████████████   | 33.9MB 69.0MB/s eta 0:00:01��████████████▌| 36.8MB 74.0MB/s eta 0:00:01
  Running setup.py install for en-core-web-sm ... done

    Linking successful
    /home/deepl/.local/lib/python3.7/site-packages/en_core_web_sm -->
    /home/deepl/.local/lib/python3.7/site-packages/spacy/data/en

    You can now load the model via spacy.load('en')



In [72]:
!python3 -m spacy download en_core_web_sm --user


    Linking successful
    /home/deepl/.local/lib/python3.7/site-packages/en_core_web_sm -->
    /home/deepl/.local/lib/python3.7/site-packages/spacy/data/en_core_web_sm

    You can now load the model via spacy.load('en_core_web_sm')



In [65]:
df["sector"].unique()

array(['Nutrition', 'Health', 'Food', 'Cross', 'Shelter', 'Protection',
       'Education', 'Livelihood', 'NFI', 'WASH', 'Agriculture',
       'Logistic'], dtype=object)

In [114]:
nlp = spacy.load('en_core_web_sm')
doc = nlp(u'The red crossmobilises staff in Mumbai')

for ent in doc.ents:
    print(ent.text, ent.start_char, ent.end_char, ent.label_)

Mumbai 32 38 GPE


In [117]:
def retrieveEntities(row):
    doc = nlp(row["preprocessed_excerpt"])
    entity_dict = {
        "FAC": 0,
        "GPE": "",  
    }
    
    for ent in doc.ents:
        if (ent.label_ in entity_dict):
            entity_dict[ent.label_] = ent.text if (ent.label_ == 'GPE') else 1
    print (entity_dict)
    return entity_dict["FAC"], entity_dict["GPE"]

In [106]:
!sed -e 's/\s\+/,/g' hdi.txt > hdi.csv

In [113]:
hdi_ranks = pd.read_csv("hdi.csv")

In [118]:
df["Infra"], df["Country"] = df.apply(retrieveEntities, axis=1)

{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': '1150mt'}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': 'india'}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}

{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0,

{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': '493000'}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FA

{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0,

{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': 'malaysia'}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'

...

{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0,

{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 1, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0,

{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0,

{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0, 'GPE': ''}
{'FAC': 0,

KeyboardInterrupt: 

In [126]:
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import stopwords

def to_words(content):
    letters_only = re.sub("[^a-zA-Z]", " ", content)
    words = letters_only.lower().split()
    stops = set(stopwords.words("english"))
    meaningful_words = [w for w in words if not w in stops]
    return ( " ".join(meaningful_words))

def tfidf_extraction(text_corpus):
    processed_text = text_corpus
    print (processed_text)
    vectorizer = TfidfVectorizer(analyzer='word')
    try:
        result = vectorizer.fit_transform(processed_text)
        feature_array = np.array(vectorizer.get_feature_names())
        tfid_sorting = np.argsort(result.toarray()).flatten()[::-1]

        n=10

        top_n = feature_array[tfid_sorting][:n]
    except:
        top_n = np.array([])

    return top_n

def keyword_generation(row):
        return ','.join(tfidf_extraction(to_words(row['preprocessed_excerpt']).split(',')))

In [127]:
df['Keywords'] = df.apply(keyword_generation, axis=1) 

['child five risk acute malnutrition']
['cholera case suspected october alone']
['people need urgent food assistance']
['health facility destroyed']
['million people need aid']
['humanitarian need said include access sufficient supply quality water education shelter child protection health nutrition']
['people urgent food insecurity located area per cent population affected hurricane include place livelihood activity related agriculture livestock fishing almost completely destroyed crops farm equipment stocks trade']
['follow governments announcement close temporary shelter plan establish camps grow fear displaced people cause overcrowd home family friends streets']
['exacerbate preexisting displacement crisis ten thousand haitian return neighboring dominican republic concern increased safety child families especially increased risk food insecurity malnutrition vulnerability violence include sex genderbased violence sgbv exploitations disease']
['agency expressed serious concern risk i

['lake chad basin crisis acute million people require emergency assistance financial need almost tripled since last year half million severely malnourished child need immediate help survive mali humanitarian situation stable remains extremely worrying due insecurity said mr toby lanzer']
['fund required appeal based country humanitarian response plan cameroon mali niger nigeria chad well humanitarian work plan burkina faso mauritania senegal']
['appeal involves partner organisation work together save life protect asset vulnerable communities part strategy complements lifesaving relief operation early response closer partnership government development organisations']
['one five family sahel continues extremely vulnerable million people fled homes million people face food insecurity million urgently need aid malnutrition continues reach critical level region particularly chad northeast nigeria prevalence global acute malnutrition high per cent double emergency threshold']
['appeal involv

['muac rate threshold concern garissa isiolo mandera marsabit meru north samburu turkana wajir highest samburu significant rise muac rate previous month kilifi kajiado significant fall previous month garissa embu rate fell counties attributed integrated health outreach former increased milk consumption latter']
['insecurity conflict continue undermine food security number asal counties violent incident reported west pokot border trans nzoia elgeyo marakwet counties former led loss life latter caused closure market turkana conflict erupted lomelo area close border pokot tension also high part isiolo gafarsa kombola belgesh far without incident insecurity increased isiolomeru border area']
['suicide blast rocked lashkargah city provincial capital southern helmand province afghanistan eyewitness area say blast likely taken place close compound security forces preliminary report indicate least people killed attack several others wounded']
['december case confirmed probable suspected includ

['least people arrested crimea since march charge plan act terrorism sabotage evidence however based footage like dmitry shtyblikovs arrest filmed confessions detainee later stated extracted torture']
['large part southern thailand remain floodwaters week heavy monsoon rain government scrambled emergency aid million affected residents']
['widespread flooding damaged five government installations roadsand bridges']
['government started build temporary bridge replace damaged bridge said provinces chief administration officer somporn patchimphet']
['also said provinces bangsapan district hospital flooded last night force authority evacuate patient higher floor nearby hospitals']
['flooding also shuttered airport nakhon si thammarat train deep south']
['nigerian government make considerable effort recover chibok girl still boko harams custody concerned victim less well publicised mass abduction benefited comparable effort secure release']
['twin taliban blast struck near afghan parliament 

['million people require assistance shelter nonfood item nfis management collective centre living people million area acute need represents enormous per cent increase since late result largescale population movement month conflict']
['nearly million people need protection assistance include million living acutely affected areas']
['million child yemen currently school represents per cent million schoolaged child includes idp children']
['united arab emirates says five diplomat died bombing afghanistans kandahar killed least people wounded others include juma alkaabi uae ambassador afghanistan official emirati news agency wam said official mission carry humanitarian educational development projects']
['another activist civil progressive alliance pakistan cpap president samar abbas reportedly gone miss federal capital']
['undocumented afghan spontaneously returned deported pakistan']
['prefecture nanagribizi subprefecture mbr mbr since december beginning clash armed group village morouba

...

['child five suffer global acute malnutrition gam include case severe acute malnutrition sam need strengthen malnutrition treatment child displaced host populations need increase malnutrition screen among child fivethe ngo irc screened pregnant nursing woman daressalam refugee camp woman affected sam mam']
['necessary protect displaced people multisector referral response mechanisms people face specific protection risks include child women need enhanced community protection mechanismsin june protection incident reported site covered protection monitoring unhcr chadian red cross crt case genderbased violence documented gbv subcluster june limited number location fouli kaya departments psychological violence account per cent cases victim women per cent internally displacedin total case gbv documented since beginning year per cent april june']
['displaced people need enhanced epidemiological surveillance displaced people host community need improved access primary health care access medic

['survey done ministry water resource care international greater freetown flooded communities show alarm contamination faecal coliforms water source actively used community wells moreover lack residual chlorine']
['heavy rain also destroyed homes include home traditional huts director civil protection said head cattle also decimated water caused extensive material damage store almost eight region country destroy grain fields orchard roads end last week niger authority called thousand resident niamey evacuate house threatened rise water levels asked victim temporarily relocate schools']
['august suspectedconfirmed cholera case deaths reported two health district burundi']
['burundi experienced small cholera outbreak second week july cluster six case confirmed bujumbura capital city reported weekly bulletin week current event index case reportedly returned day disease onset karamba south kivu province democratic republic congo cholera case reported past weeks ongoing cholera outbreak dem

['doctors dry strike continued public hospital tuesday august th kinshasa patient hospital either abandoned sent back private centers patient evacuated patient said disoriented patient front kinshasa reference general hospital report almost public hospital capital accord radio okapi reporters']
['ecuadors doctor monday august th radicalized strike movement across province means patient abandoned major public medical training certain patient admitted hospital treated']
['kasa central doctor affiliated national syndicate doctor synamed decide observe thursday august minimum service hospitals accord provincial executive secretary association dr berry beya white coat require salary indexed current exchange rate one us dollar one thousand five hundred fifty congolese francs']
['nutritional situation result nutritional survey carried health zone affected current crisis province kasa one shows rate mag respectively percent percent rate emergency threshold require emergency intervention save l

['total police officer admitted various hospital choleralike symptoms fortyfive officer deployed nairobi ahead supreme court rule friday infected reside multimedia university hotel rongai']
['highest number suspected meningitis case reported amanat alasimah governorate case governorates report high number case include taiz case dhamar case ibb case al hodeida cases aden cases governorates reported high number case host main referral hospital serve sentinel site national bacterial meningitis surveillance programme yemen']
['compared number health facility report bacterial meningitis case yemen increased please see box reported case bacterial meningitis appeared increased expected however analysis current years trend compare previous years evidence increase meningitis case observed two sample tested far found positive epidemic strain known caused epidemic meningococcal meningitis countries primarily african meningitis beltthe current trend cases observed measured weekly attack rate pleas

['access essential services already precarious state crisis deteriorated systematic registration new born children example limited civil registry several district destroyed approximately school closed result children per cent girls longer school attend school outside communities health centre could provide limited services even prior crisis increasingly pressure assist high number newly displaced person treat seriously injured cameroonian citizen event terrorist attack access drinking water sanitation continues challenge size population need increases']
['population live border area identity document risk displacement including occasion sent back forth arbitrarily across border risk statelessness increased include cameroonian nationals']
['cross river record death month floodfifteen people lost life severe flooding community cross river july august yearthe directorgeneral cross river state emergency management agency mr john inaku made disclosure assess extent damage flooded area calab

In [129]:
df

sector                                          subsector  \
0        Nutrition                                      Breastfeeding   
1           Health                             Health status and risk   
2             Food                                                NaN   
3           Health                                                NaN   
4            Cross                                                NaN   
5            Cross                                                NaN   
6             Food                                                NaN   
7          Shelter                Shelter infrastructure and material   
8       Protection  Sexual violence and other forms of Gender Base...   
9       Protection  Sexual violence and other forms of Gender Base...   
10           Cross                                                NaN   
11            Food                                                NaN   
12            Food                                                NaN   
13            Food                                                NaN   
14            Food                                                NaN   
15          Health                                                NaN   
16       Nutrition                                     Undernutrition   
17          Health                             Health status and risk   
18       Nutrition                                                NaN   
19          Health                                                NaN   
20       Education                                                NaN   
21          Health                                                NaN   
22      Livelihood                                                NaN   
23          Health                          Health system performance   
24             NFI                                                NaN   
25            WASH                                                NaN   
26      Protection                                                NaN   
27      Protection                                                NaN   
28      Protection                                                NaN   
29            Food                                                NaN   
...            ...                                                ...   
16436        Cross                                                NaN   
16437         Food                                                NaN   
16438  Agriculture                                                NaN   
16439  Agriculture                                                NaN   
16440    Education                                                NaN   
16441      Shelter                                                NaN   
16442      Shelter                                                NaN   
16443       Health                                                NaN   
16444      Shelter                                                NaN   
16445    Education                                                NaN   
16446  Agriculture                                                NaN   
16447    Nutrition                                                NaN   
16448    Nutrition                                                NaN   
16449   Protection                                                NaN   
16450   Protection                                                NaN   
16451      Shelter                                                NaN   
16452         Food                                                NaN   
16453       Health                                                NaN   
16454       Health                                                NaN   
16455         Food                                                NaN   
16456         WASH                                                NaN   
16457   Protection                                                NaN   
16458         Food                                                NaN 

In [130]:
import gensim.models.word2vec as w2v

In [173]:
text_corpus = []
for keywords in df['Keywords']:
    words = keywords.lower().split()
    text_corpus.append(words)


num_features = 10

min_word_count = 1

num_workers = -1

# Context window length.
context_size = 2

# Downsample setting for frequent words.
#0 - 1e-5 is good for this
downsampling = 1e-1

# Seed for the RNG, to make the results reproducible.
#random number generator
#deterministic, good for debugging
seed = 2

key2vec = w2v.Word2Vec(
    sg=1,
    seed=seed,
    workers=num_workers,
    size=num_features,
    min_count=min_word_count,
    window=context_size,
    sample=downsampling
)

key2vec.build_vocab(text_corpus)

In [174]:
import os
key2vec.train(text_corpus, total_examples=key2vec.corpus_count, epochs=10)
if not os.path.exists("trained"):
    os.makedirs("trained")
key2vec.save(os.path.join("trained", "key2vec.w2v"))

In [160]:
key2vec.corpus_total_words

16463

/home/deepl/.local/lib/python3.7/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  """Entry point for launching an IPython kernel.


[('health,collapse,public,billion,service,cent,sector,per,central,october',
  0.9133769273757935),
 ('years,incidence,every,drought,educate,increased,increase,inadequate,historically,good',
  0.9061188697814941),
 ('mosul,school,displaced,age,among,child,city,come,currently,eastern',
  0.8924741148948669),
 ('zemiomboki,supplied,situation,safe,poorly,occupation,obo,market,groups,good',
  0.8897601962089539),
 ('son,several,include,innocent,woman,jewelry,abdul,also,arz,attacks',
  0.8768600225448608),
 ('mai,january,killed,several,cause,group,fishermen,fire,extorted,edward',
  0.8734984397888184),
 ('water,week,level,boane,city,country,critical,dam,district,dry',
  0.8633397817611694),
 ('food,wfp,assistance,gap,eastern,half,fundinga,funding,forced,financial',
  0.8583517670631409),
 ('woman,displaced,farming,food,aid,also,back,bonte,child,desperately',
  0.8517349362373352),
 ('humanitarian,particularly,half,attack,attributed,baidoa,belet,central,collateral,damage',
  0.846033215522766

In [171]:
df

sector                                          subsector  \
0        Nutrition                                      Breastfeeding   
1           Health                             Health status and risk   
2             Food                                                NaN   
3           Health                                                NaN   
4            Cross                                                NaN   
5            Cross                                                NaN   
6             Food                                                NaN   
7          Shelter                Shelter infrastructure and material   
8       Protection  Sexual violence and other forms of Gender Base...   
9       Protection  Sexual violence and other forms of Gender Base...   
10           Cross                                                NaN   
11            Food                                                NaN   
12            Food                                                NaN   
13            Food                                                NaN   
14            Food                                                NaN   
15          Health                                                NaN   
16       Nutrition                                     Undernutrition   
17          Health                             Health status and risk   
18       Nutrition                                                NaN   
19          Health                                                NaN   
20       Education                                                NaN   
21          Health                                                NaN   
22      Livelihood                                                NaN   
23          Health                          Health system performance   
24             NFI                                                NaN   
25            WASH                                                NaN   
26      Protection                                                NaN   
27      Protection                                                NaN   
28      Protection                                                NaN   
29            Food                                                NaN   
...            ...                                                ...   
16436        Cross                                                NaN   
16437         Food                                                NaN   
16438  Agriculture                                                NaN   
16439  Agriculture                                                NaN   
16440    Education                                                NaN   
16441      Shelter                                                NaN   
16442      Shelter                                                NaN   
16443       Health                                                NaN   
16444      Shelter                                                NaN   
16445    Education                                                NaN   
16446  Agriculture                                                NaN   
16447    Nutrition                                                NaN   
16448    Nutrition                                                NaN   
16449   Protection                                                NaN   
16450   Protection                                                NaN   
16451      Shelter                                                NaN   
16452         Food                                                NaN   
16453       Health                                                NaN   
16454       Health                                                NaN   
16455         Food                                                NaN   
16456         WASH                                                NaN   
16457   Protection                                                NaN   
16458         Food                                                NaN 

In [182]:
def getKeywordVector(row):
    try:
        return key2vec.wv[row["Keywords"]]
    except:
        return np.zeros(10)
       

In [183]:
df["keyword_vector"] = df.apply(getKeywordVector, axis=1)

In [184]:
df

sector                                          subsector  \
0        Nutrition                                      Breastfeeding   
1           Health                             Health status and risk   
2             Food                                                NaN   
3           Health                                                NaN   
4            Cross                                                NaN   
5            Cross                                                NaN   
6             Food                                                NaN   
7          Shelter                Shelter infrastructure and material   
8       Protection  Sexual violence and other forms of Gender Base...   
9       Protection  Sexual violence and other forms of Gender Base...   
10           Cross                                                NaN   
11            Food                                                NaN   
12            Food                                                NaN   
13            Food                                                NaN   
14            Food                                                NaN   
15          Health                                                NaN   
16       Nutrition                                     Undernutrition   
17          Health                             Health status and risk   
18       Nutrition                                                NaN   
19          Health                                                NaN   
20       Education                                                NaN   
21          Health                                                NaN   
22      Livelihood                                                NaN   
23          Health                          Health system performance   
24             NFI                                                NaN   
25            WASH                                                NaN   
26      Protection                                                NaN   
27      Protection                                                NaN   
28      Protection                                                NaN   
29            Food                                                NaN   
...            ...                                                ...   
16436        Cross                                                NaN   
16437         Food                                                NaN   
16438  Agriculture                                                NaN   
16439  Agriculture                                                NaN   
16440    Education                                                NaN   
16441      Shelter                                                NaN   
16442      Shelter                                                NaN   
16443       Health                                                NaN   
16444      Shelter                                                NaN   
16445    Education                                                NaN   
16446  Agriculture                                                NaN   
16447    Nutrition                                                NaN   
16448    Nutrition                                                NaN   
16449   Protection                                                NaN   
16450   Protection                                                NaN   
16451      Shelter                                                NaN   
16452         Food                                                NaN   
16453       Health                                                NaN   
16454       Health                                                NaN   
16455         Food                                                NaN   
16456         WASH                                                NaN   
16457   Protection                                                NaN   
16458         Food                                                NaN 

In [224]:
from sklearn.model_selection import train_test_split
train, test = train_test_split(df, test_size=0.1, random_state=42)

In [225]:
def tokenize_text(text):
    tokens = []
    for sent in nltk.sent_tokenize(text):
        for word in nltk.word_tokenize(sent):
            if len(word) < 2:
                continue
            tokens.append(word.lower())
    return tokens

In [226]:
from gensim.models.doc2vec import TaggedDocument
nltk.download('punkt')
train_tagged = train.apply(
    lambda r: TaggedDocument(words=tokenize_text(r['preprocessed_excerpt']), tags=[r.sector]), axis=1)
test_tagged = test.apply(
    lambda r: TaggedDocument(words=tokenize_text(r['preprocessed_excerpt']), tags=[r.sector]), axis=1)

[nltk_data] Downloading package punkt to /home/deepl/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [230]:
labels, features = vec_for_learning(model_dbow, train_tagged)
y_test, X_test = vec_for_learning(model_dbow, test_tagged)

In [231]:
train["docvector"] = features
test["docvector"] = X_test

/home/deepl/.local/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.
/home/deepl/.local/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [233]:
def combineVectors(row):
    return np.concatenate((row["docvector"], row["keyword_vector"]))

train["combined_vector"] = train.apply(combineVectors, axis=1)
test["combined_vector"] = test.apply(combineVectors, axis=1)

/home/deepl/.local/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.
/home/deepl/.local/lib/python3.7/site-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """


In [248]:
features = train["combined_vector"]

1647